# Lecture 17 – Data 100, Summer 2024

Data 100, Summer 2024

[Acknowledgments Page](https://ds100.org/sp24/acks/)

In [1]:
import pandas as pd
import numpy as np
import plotly.express as px


---

## A Random Variable $X$

Our probability distribution of $X$, shown as a table:

In [2]:
# Our random variable X
dist_df = pd.DataFrame({"x": [3, 4, 6, 8],
                        "P(X = x)": [0.1, 0.2, 0.4, 0.3]})
dist_df

x  P(X = x)
0  3       0.1
1  4       0.2
2  6       0.4
3  8       0.3

In [3]:
fig = px.bar(dist_df, x="x", y="P(X = x)", title="Distribution of X")
# fig.write_image("distX.png", "png",scale=2)
fig

Let's use this probability distribution to generate a table of $X(s)$, i.e., random variable values for many many draws (with replacement).

In [4]:
N = 80000
samples = np.random.choice(
    dist_df["x"], # Draw from these choiecs
    size=N, # This many times
    p=dist_df["P(X = x)"]) # According to this distribution

sim_df = pd.DataFrame({"X(s)": samples})
sim_df

X(s)
0         6
1         4
2         6
3         6
4         6
...     ...
79995     8
79996     6
79997     6
79998     3
79999     4

[80000 rows x 1 columns]

<br/><br/>
Let's check how well this simulated sample matches our probability distribution!

In [7]:
fig = px.histogram(sim_df, x="X(s)", title="Empirical distribution of X", 
                   histnorm="probability")
# fig.write_image("empirical_dist.png", "png",scale=2)
fig

In [8]:
print("Simulated E[X]:", sim_df['X(s)'].mean())
print("Simulated Var[X]:", sim_df['X(s)'].var())

Simulated E[X]: 5.89535
Simulated Var[X]: 2.9003596319953995


In [9]:
E_x = dist_df["x"] @ dist_df["P(X = x)"]
print("E[X]:",E_x)

E[X]: 5.9


In [10]:
Var_x = dist_df["x"]**2 @ dist_df["P(X = x)"] - E_x**2
print("Var[X]:", Var_x)

Var[X]: 2.8900000000000006


<br/><br/>

---

# Sum of 2 Dice Rolls

Here's the distribution of a single die roll:

In [11]:
roll_df = pd.DataFrame({"x": [1, 2, 3, 4, 5, 6],
                        "P(X = x)": np.ones(6)/6})
roll_df

x  P(X = x)
0  1  0.166667
1  2  0.166667
2  3  0.166667
3  4  0.166667
4  5  0.166667
5  6  0.166667

In [12]:
fig = px.bar(roll_df, x="x", y="P(X = x)", title="Distribution of X")
# fig.write_image("die.png", "png",scale=2)
fig

Let $X_1, X_2$ are the outcomes of two dice rolls. Note $X_1$ and $X_2$ are i.i.d. (independent and identically distributed).

Below I call a helper function `simulate_iid_df`, which simulates an 80,000-row table of $X_1, X_2$ values. It uses `np.random.choice(arr, size, p)` [link](https://numpy.org/doc/stable/reference/random/generated/numpy.random.choice.html) where `arr` is the array the values and `p` is the probability associated with choosing each value. If you're interested in the implementation details, scroll up.

In [13]:
N = 80000

sim_rolls_df = pd.DataFrame({
    "X_1": np.random.choice(roll_df["x"], size = N, p = roll_df["P(X = x)"]),
    "X_2": np.random.choice(roll_df["x"], size = N, p = roll_df["P(X = x)"])
})

sim_rolls_df

X_1  X_2
0        3    5
1        2    1
2        6    3
3        2    4
4        1    5
...    ...  ...
79995    5    1
79996    1    6
79997    6    4
79998    3    1
79999    1    3

[80000 rows x 2 columns]

Define the following random variables, which are functions of $X_1$ and $X_2$:
* $Y = X_1 + X_1 = 2 X_1$
* $Z = X_1 + X_2$

We can use our simulated values of $X_1, X_2$ to create new columns $Y$ and $Z$:

In [14]:
sim_rolls_df['Y'] = 2 * sim_rolls_df['X_1']
sim_rolls_df['Z'] = sim_rolls_df['X_1'] + sim_rolls_df['X_2']
sim_rolls_df

X_1  X_2   Y   Z
0        3    5   6   8
1        2    1   4   3
2        6    3  12   9
3        2    4   4   6
4        1    5   2   6
...    ...  ...  ..  ..
79995    5    1  10   6
79996    1    6   2   7
79997    6    4  12  10
79998    3    1   6   4
79999    1    3   2   4

[80000 rows x 4 columns]

Now that we have simulated samples of $Y$ and $Z$, we can plot histograms to see their distributions!


In [15]:
px.histogram(sim_rolls_df[["Y", "Z"]].melt(), x="value", color="variable", 
             barmode="overlay", histnorm="probability",
             title="Empirical Distributions")


In [16]:
pd.DataFrame([
    sim_rolls_df[["Y", "Z"]].mean().rename("Mean"),
    sim_rolls_df[["Y", "Z"]].var().rename("Var"),
    np.sqrt(sim_rolls_df[["Y", "Z"]].var()).rename("SD")
])

Y         Z
Mean   6.979900  6.984400
Var   11.696242  5.842730
SD     3.419977  2.417174

<br/><br/>

---
# Gambling
Suppose you win cash based on the number of heads you get in a series of 20 coin flips. Let Xi = 1 if the i-th coin is heads, 0 otherwise

Which payout strategy would you choose? Hint: Compare expectations and variances

* $\large Y_A = 10 X_1 + 10 X_2 $
* $\large Y_B = \sum\limits_{i=1}^{20} X_i$
* $\large Y_C = 20 X_1$

First let's construct the probability distribution for a single coin. This will let us flip 20 IID coins later.

In [17]:
# First construct probability distribution for a single fair coin
p = 0.5
coin_df = pd.DataFrame({"x": [1, 0], # [Heads, Tails]
                        "P(X = x)": [p, 1 - p]})
coin_df

x  P(X = x)
0  1       0.5
1  0       0.5

## Choice A:
$\large Y_A = 10 X_1 + 10 X_2 $

In [22]:
N = 10000

np.random.rand(N,2) < p

array([[False, False],
       [False,  True],
       [ True, False],
       ...,
       [False,  True],
       [False, False],
       [False,  True]])

In [23]:
sim_flips = pd.DataFrame(
    {"Choice A": np.sum((np.random.rand(N,2) < p) * 10, axis=1)})
sim_flips

Choice A
0           10
1           20
2           10
3           20
4            0
...        ...
9995        10
9996        10
9997         0
9998        20
9999        10

[10000 rows x 1 columns]

## Choice B:

$\large Y_B = \sum\limits_{i=1}^{20} X_i$

In [24]:
sim_flips["Choice B"] = np.sum((np.random.rand(N,20) < p), axis=1)
sim_flips

Choice A  Choice B
0           10        10
1           20         9
2           10         6
3           20         8
4            0        12
...        ...       ...
9995        10         9
9996        10         7
9997         0        10
9998        20        11
9999        10        10

[10000 rows x 2 columns]

## Choice C:

$\large Y_C = 20 X_1$

In [25]:
sim_flips["Choice C"] = 20  * (np.random.rand(N,1) < p) 
sim_flips

Choice A  Choice B  Choice C
0           10        10        20
1           20         9        20
2           10         6         0
3           20         8         0
4            0        12         0
...        ...       ...       ...
9995        10         9         0
9996        10         7        20
9997         0        10        20
9998        20        11         0
9999        10        10        20

[10000 rows x 3 columns]

<br/>
Let's visualize these empirical distributions (simulations):

In [26]:
px.histogram(sim_flips.melt(), x="value", facet_row="variable", 
             barmode="overlay", histnorm="probability",
             title="Empirical Distributions",
             width=600, height=600)

In [27]:
pd.DataFrame([
    sim_flips.mean().rename("Mean"),
    sim_flips.var().rename("Var"),
    np.sqrt(sim_flips.var()).rename("SD")
])

Choice A  Choice B   Choice C
Mean  10.043000  9.968800   9.824000
Var   50.353186  5.103937  99.979022
SD     7.095998  2.259189   9.998951

<br/><br/><br/>

---

# From Population to Sample

Remember the population distribution we looked at earlier:

In [28]:
dist_df

x  P(X = x)
0  3       0.1
1  4       0.2
2  6       0.4
3  8       0.3

In [29]:
# A population generated from the distribution
N = 100000
all_samples = np.random.choice(dist_df["x"], N, p=dist_df["P(X = x)"])
sim_pop_df = pd.DataFrame({"X(s)": all_samples})
sim_pop_df

X(s)
0         8
1         3
2         6
3         6
4         6
...     ...
99995     4
99996     8
99997     8
99998     8
99999     8

[100000 rows x 1 columns]

<br/><br/><br/>
Suppose we draw a sample of size 100 from this giant population.

We are performing **Random Sampling with Replacement:** `df.sample(n, replace=True)` ([link](https://pandas.pydata.org/docs/reference/api/pandas.DataFrame.sample.html))

In [30]:
n = 100      # Size of our sample
sample_df = (
             sim_pop_df.sample(n, replace=True)
             # Some reformatting below
             .reset_index(drop=True)
             .rename(columns={"X(s)": "X"})
            )
sample_df

X
0   6
1   6
2   6
3   6
4   6
.. ..
95  4
96  8
97  4
98  6
99  6

[100 rows x 1 columns]

Our **sample distribution** (n = 100):

In [31]:
px.histogram(sample_df, x="X", histnorm="probability", title="Sample (n = 100)")

<br/>

Compare this to our **original population** (N = 80,000):

In [32]:
px.histogram(sim_df, x="X(s)", histnorm="probability", title="Population of X")

In [33]:
pd.DataFrame(
    {"Sample": [sample_df["X"].mean(), sample_df["X"].var(), np.sqrt(sample_df["X"].var())],
     "Population": [sim_df["X(s)"].mean(), sim_df["X(s)"].var(), np.sqrt(sim_df["X(s)"].var())]})

Sample  Population
0  5.730000    5.895350
1  2.057677    2.900360
2  1.434460    1.703044